In [1232]:
import pandas as pd, numpy as np, json, os

In [1233]:
# os.chdir('E:/Onedrive - Lancaster University/datarepo/influence/ro')
os.chdir('C:/users/csala/Onedrive - Lancaster University/datarepo/influence/ro')

In [1234]:
nmembers=json.loads(open('data/nmembers.json','r').read())

In [1235]:
img=json.loads(open('data/img.json','r').read())

In [1236]:
deaths=json.loads(open('data/deaths.json','r').read())

In [1238]:
# os.chdir('E:/Skydrive/Github/influence/ro')
os.chdir('C:/users/csala/Onedrive/Github/influence/ro')

In [1239]:
legs={'2016':['2016-12-21','2019-07-01'],
'2012':['2012-12-20','2016-12-21'],
'2008':['2008-12-19','2012-12-20'],
'2004':['2004-12-19','2008-12-13'],
'2000':['2000-12-15','2004-11-30'],
'1996':['1996-11-27','2000-11-30'],
'1992':['1992-10-28','1996-11-22'],
'1990':['1990-06-19','1992-10-16']}

In [1240]:
import altair as alt

In [1241]:
from colorthief import ColorThief
import requests

In [1242]:
party_imgs={}
for p in img['party']:
    i=img['party'][p]['img']
    try: 
        color_thief = ColorThief('img/'+p.lower()+'.png')
        rgb_color=color_thief.get_color(quality=1)        
        z='#%02x%02x%02x' % rgb_color
    except:
        try:
            color_thief = ColorThief('img/'+p.lower()+'.jpg')
            rgb_color=color_thief.get_color(quality=1)        
            z='#%02x%02x%02x' % rgb_color
        except:
            z='grey'  
    party_imgs[p]=z

In [1243]:
party_imgs['UDMR']='green'
party_imgs['RMDSZ']='green'
party_imgs['PNL']='#f4d42c'
party_imgs['ALDE']='#046cab'

In [1244]:
colors=pd.DataFrame(party_imgs,index=['Color']).T

In [1245]:
plinks={}
for i in colors.index:
    print('"'+i+'":"'+colors.loc[i]['Color']+'",')
    plinks[i]='https://influence.csaladen.es/ro/img/'+i.lower()+'.png'

"PSD":"#dc2c24",
"FSN":"grey",
"PDL":"grey",
"PNL":"#f4d42c",
"PNTCD":"#04843c",
"PRM":"#0d5ca4",
"PDSR":"#ebedf1",
"PC":"#96c2f2",
"UDMR":"green",
"PAC":"grey",
"MER":"grey",
"Fără adeziune la formaţiunea politică pentru care a candidat la alegeri":"grey",
"PD":"grey",
"PUNR":"grey",
"USR":"#04abe4",
"PP-DD":"#d7c9e0",
"UNPR":"#a8190f",
"PER":"grey",
"PUR-SL":"grey",
"FDSN":"grey",
"PSDR":"#2e2f26",
"ALDE":"#046cab",
"PMP":"#0484cc",
"PNL-AT":"grey",
"PDAR":"grey",
"PSM":"grey",
"PL'93":"grey",
"FC":"#1d7aad",
"PNL-CD":"grey",
"ULB":"grey",
"PLS":"grey",
"PAR":"grey",
"GDC":"grey",
"AUR":"grey",
"FER":"grey",
"PRNR":"grey",
"PDM":"grey",
"PTLDR":"grey",
"#PRES##GRUP#Grupul parlamentaral Partidului Poporului - Dan Diaconescu (până în mar.":"grey",
"#SECR##GRUP#Grupul parlamentaral Partidului Unităţii Naţionale Române":"grey",
"#VP##GRUP#Grupul parlamentaral Uniunii Naţionale pentru Progresul României (Grupul Progresist)":"grey",
"#PRES##GRUP#Grupul parlamentarALDE (Alianţa liberalilor 

Members

In [1246]:
szen=['🔼 Szenátus','🔽 Képviselőház']
szen2=['Senat','Camera Deputaților']

In [1247]:
istart=legs['1990'][0]
iend=legs['2016'][1]

In [1248]:
ro_months={'ian.':'Jan',
          ' ia ':' Jan ',
          'feb.':'Feb',
          'mar.':'Mar',
          'apr.':'Apr',
          'mai':'May',
          'iun.':'Jun',
          ' iu ':' Jun ',
          'iul.':'Jul',
          'aug.':'Aug',
          'sep.':'Sep',
          'oct.':'Oct',
          'noi.':'Nov',
          'dec.':'Dec',
          'ianuarie':'Jan',
          'februarie':'Feb',
          'martie':'Mar',
          'aprilie':'Apr',
          'mai':'May',
          'iunie':'Jun',
          'iulie':'Jul',
          'august':'Aug',
          'septembrie':'Sep',
          'octombrie':'Oct',
          'noiembrie':'Nov',
          'decembrie':'Dec'}
def date_ro(d,s=True):
    if 'prezent' in d:
        t=pd.to_datetime(legs['2016'][1])
    else:
        ds=d.split(' ')
        x=ds[1].replace('0201','2001').replace('0092','1992')
        t=pd.to_datetime(ro_months[ds[0].strip()]+' '+x)
    if s: return str(t)[:10]
    else: return t

In [1249]:
def replace_all(text, dic):
    for i in dic:
        text = text.replace(i, dic[i])
    return text

In [1250]:
m=nmembers['Antonescu George Crin Laurentiu | 1959-09-21']
data=[]
for p in m['Parties']:
    start=pd.to_datetime(p['start'])
    end=pd.to_datetime(p['end'])    
    d={}
    d['Name']=m['Name']['full']
    d['Csoportok']=p['party']
    d['Típus']='Párt'
    d['start']=start
    d['end']=end
    d['duration']=pd.to_timedelta(end-start).days
    data.append(d)
    d=dict(d)
    d['Csoportok']=p['judet']
    d['Típus']='Megye'
    data.append(d)
for p in m['Countries']:
    start=pd.to_datetime(p['start'])
    end=pd.to_datetime(p['end'])    
    d={}
    d['Name']=m['Name']['full']
    d['Csoportok']=p['country']
    d['Típus']='Ország'
    d['start']=start
    d['end']=end
    d['duration']=pd.to_timedelta(end-start).days
    data.append(d)
for p in m['Groups']:
    start=pd.to_datetime(p['start'])
    end=pd.to_datetime(p['end'])    
    d={}
    d['Name']=m['Name']['full']
    d['Csoportok']=p['group'].replace('Comisia pentru','').replace('Comisia','').strip().capitalize()
    d['Típus']='Bizottság'
    d['start']=start
    d['end']=end
    d['duration']=pd.to_timedelta(end-start).days
    data.append(d)
for pi,p in enumerate(m['Link']):
    start=pd.to_datetime(legs[p[-10:-6]][0])
    end=pd.to_datetime(legs[p[-10:-6]][1])    
    d={}
    d['Name']=m['Name']['full']
    d['Típus']='Kamara'
    kamara=m['Camera'][pi]
    pres=''
    if '#' in kamara:
        pres='#'+kamara.split('#')[1]+'#'
        if ('din ') in kamara:
            b=dict(d)
            b['Csoportok']=szen2[int(p[-1])-1]
            b['start']=start
            start=max(start,date_ro(kamara[kamara.find('din ')+4:].strip(),False))
            b['end']=start
            b['duration']=pd.to_timedelta(end-start).days
            data.append(b)
        if ('până în ') in kamara:
            b=dict(d)
            b['Csoportok']=szen2[int(p[-1])-1]
            b['end']=end
            end=min(end,date_ro(kamara[kamara.find('până în ')+8:].strip(),False))
            b['start']=end
            b['duration']=pd.to_timedelta(end-start).days
            data.append(b)
    d['Csoportok']=pres+szen2[int(p[-1])-1]
    d['start']=start
    d['end']=end
    d['duration']=pd.to_timedelta(end-start).days
    data.append(d)
ef=pd.DataFrame(data)
eord=ef.groupby('Típus').sum()
eord['duration']=[1,60,30,4,50]
eord.columns=['order']
ef=ef.set_index('Típus').join(eord).reset_index()

In [1251]:
alt.Chart(ef,
          title=m['Name']['full']
         ).mark_bar().encode(
    x=alt.X('start:T',title=''),
    x2='end:T',
    y=alt.Y('Csoportok:N',title='',
            sort=alt.EncodingSortField(field="order", op="mean", order='descending')),
    color=alt.Color('Típus:N',
        sort=alt.EncodingSortField(field="order", op="mean", order='descending'))
)

<VegaLite 3 object>

If you see this message, it means the renderer has not been properly enabled
for the frontend that you are using. For more information, see
https://altair-viz.github.io/user_guide/troubleshooting.html


Save JSON

In [1252]:
def party_normalizer(party):
    if party in ['N/A','NA','NI',['NA', 'NI'],'-','Independent','Minorități',
                'Fără adeziune la formaţiunea politică pentru care a candidat la alegeri']: return '👤'
    elif party in ['ALDE RO','ALDE Romania','Partidul Conservator','Liberal Conservator',
                   'PC','Partidul Puterii Umaniste','ALDE','PUNR','PUR','PUR-SL']: return '🕊️'
    elif party in ['Forumul Democrat al Germanitor din România','FDGR']: return '⚫️'
    elif party in ['Partidul Naţional Liberal','PNL-CD',"PL'93",'PNL-AT','PAC','FC - Forţa Civică',
        'Partidul Liberal Democrat','PNL','Partida Naţională','Naţional Liberal','Alianţei Civice']: return'📐'
    elif party in ['Partidul Democrat','Partidul Democrat-Liberal','Democrat','Democrat Liberal','Democrat-Liberal în feb-2008',
                   'Democrat-Liberal','Democrat care se transforma în','PD care se transforma în','PDL în feb-2008','Dreptate şi Adevăr PNL-PD',
        'PD-L','PD','PDL']: return'🔶'
    elif party in ['Partidul Mișcarea Populară','PMP']: return '🍏'
    elif party in ['Partidul Naţional Ţaranesc Creştin Democrat','PNȚCD','PNTCD']:return '✳️'
    elif party in ['Partidul România Mare','PRM']:return '🔱'
    elif party in ['FSN','FDSN']:return '⚪️'
    elif party in ['USR']:return '🔷'
    elif party in ['PP-DD','Democrat Popular']:return '⚛️'
    elif party in ['PER','MER','PDAR','FER']:return '🍀'
    elif party in ['PSD','Partidul Social Democrat','Partidul Social Democrat + Partidul Conservator',
                   'PDSR','PSDR','PSM','P.S.D.','Uniunea PSDă -  PSD Român',
                 'democrat-agrar şi social-democrat',
                 'ecologist şi social-democrat',
                 'social-democrat al  PSD Român']:return '🌹'
    elif party in ['Romániai Magyar Demokrata Szövetség',
        'Uniunea Democrată Maghiară din România','RMDSZ','UDMR']:return '🌷'
    elif party in ['PRO Europa']: return '🧑'
    elif party in ['Uniunea Națională pentru Progresul României','UNPR']: return '🦅'
    else: 
        return '🔘'

In [1253]:
def group_party_normalizer(party):
    party0=party[:party.rfind('#')+1]
    party=party[party.rfind('#')+1:]
    party=replace_all(party,{'Grupul parlamentaral ':'',
                        'rtidului':'rtidul','fost':'',
                'Partidul Democrat Liberal':'PDL','Partidul Democrat-Liberal':'PDL',
                    'Partidul Democrat-liberal':'PDL'}).strip()
    party=replace_all(party,{'Grupul parlamentar':'','Partidul Democrat':'PD',
                            'Partidul':'','Liberal Conservator':'PC',
                            }).strip()
    if '(' in party:
        party=party.split('(')[0].strip()
    group_party_dict={'"Partida Naţională"':'Partida Naţională',
                        'Frontului Salvării Naţionale':'FSN',
                     'P.S.D.':'PSD','Conservator':'PC',
                      'Democraţiei Sociale din România':'PSD',
                      'PD care se transforma în':'PD',
                      'PDL în feb-2008':'PDL',
                      'Liberal 1993 si al  Aliantei Civice':'Alianţei Civice',
                      'Naţional Creştin Democrat':'PNTCD',
                      'Naţional Liberal':'PNL',
                      'socialist':'PSD',
                      'Naţional Ţărănesc - creştin şi democrat':'PNTCD',
                      'Naţional Ţărănesc Creştin Democrat Civic-Ecologist':'PNTCD',
                      'Naţional Ţărănesc Creştin Democrat şi al  Ecologist Român':'PNTCD',
                      'ţi neafiliaţi':'Independent',
                      'Uniunii Democrate Maghiare din România':'RMDSZ',
                      'Poporului - Dan Diaconescu':'PP-DD',
                      'România Mare':'PRM',
                      'Social Democrat':'PSD',
                      'Uniunea PSDă - PD':'PSD',
                      'Umanist din România':'PUR',
                      't neafiliat':'Independent',
                      'neafiliat':'Independent',
                      'minorităţilor naţionale':'Minorități',
                      'Uniunii Naţionale pentru Progresul României':'UNPR',
                      'Alianţei Civice':'PAC',
                      'de orientare civic-liberală':'PAC',
                      'Uniunii Salvaţi România':'USR',
                      'Partida Naţională':'PNL',
                      'Mişcarea Populară':'PMP',
                      'PD Agrar din România':'PDAR',
                      'PD în feb-2008':'PD',
                      'Unităţii Naţionale Române':'PUNR',
                      'Unităţii Naţionale a Românilor':'PUNR',
                      'deputaţilor independenţi':'Independent',
                      'i neafiliaţi':'Independent',
                      'naţional democrat':'PNTCD',
                      'progresist':'PC',
                      'Democrat Popular':'PP-DD',
                     'Dreptate şi Adevăr PNL-PD':'PDL',
                     'Uniunea PSDă -  PSD Român':'PSD',
                     'democrat-agrar şi social-democrat':'PSD',
                     'ecologist şi social-democrat':'PSD',
                     'social-democrat al  PSD Român':'PSD'
                     }
    party=party_normalizer(replace_all(party,
                group_party_dict))+' '+\
                replace_all(party,group_party_dict)
    return party0+party

In [1254]:
def party_writer(party):
    if party in ['Romániai Magyar Demokrata Szövetség',
        'Uniunea Democrată Maghiară din România','RMDSZ','UDMR']:return 'RMDSZ'
    elif party in ['Uniunea PSDă -  PSD Român',
 'democrat-agrar şi social-democrat',
 'ecologist şi social-democrat',
 'social-democrat al  PSD Român']:
        return 'PSD'
    elif party in ['Fără adeziune la formaţiunea politică pentru care a candidat la alegeri']:
        return 'Independent'
    else: 
        return party

In [1256]:
# megyek=json.loads(open('E:/Skydrive/Github/universal/ro/hun_megyek.json','r').read())
megyek=json.loads(open('C:/users/csala/Onedrive/Github/universal/ro/hun_megyek.json','r').read())
megyek['La nivel national']='Országos'

In [1257]:
r={
"Buget, finanţe şi bănci":"Pénzügy",
"Drepturile omului, culte şi problemele minorităţilor naţionale":"Emberi jogok, kisebbségek",
"Economică":"Gazdaság, ipar",
"Politică economică, reformă şi privatizare":"Gazdaság, ipar",
"Politică externă":"Külpolitika, diaszpóra",
"Învăţământ, ştiinţă, tineret, sport":"Oktatás, tudomány, sport",
"Cultură, arte, mijloace de informare în masă":"Művészet, média",
"Juridică, de disciplină şi imunităţi":"Parlament",
"Regulament":"Parlament",
"Agricultură, silvicultură, industrie alimentară şi servicii specifice":"Mezőgazdaság, erdők",
"Buget şi finanţe":"Pénzügy",
"Industrii şi servicii":"Gazdaság, ipar",
"Tehnologia informaţiei şi comunicaţiilor":"Infrastruktúra, energia, kommunikáció",
"Afaceri europene":"Európa",
"Agricultură, silvicultură şi dezvoltare rurală":"Mezőgazdaság, erdők",
"Muncă, familie şi protecţie socială":"Munka, szociális és családi ügyek",
"Cultură, artă şi mijloace de informare în masă":"Művészet, média",
"Drepturile omului, culte şi minorităţi":"Emberi jogok, kisebbségek",
"Muncă şi protecţie socială":"Munka, szociális és családi ügyek",
"Buget, finanţe, activitate bancară şi piaţă de capital":"Pénzügy",
"Economică, industrii şi servicii":"Gazdaság, ipar",
"Privatizare şi administrarea activelor statului":"Állami ügyek",
"Învăţământ, ştiinţă, tineret şi sport":"Oktatás, tudomány, sport",
"Administraţie publică, organizarea teritoriului şi protecţia mediului":"Közigazgatás, környezetvédelem",
"Egalitatea de şanse":"Munka, szociális és családi ügyek",
"Specială pentru modificarea şi completarea regulamentului senatului":"Parlament",
"Comunităţile de români din afara graniţelor ţării":"Külpolitika, diaszpóra",
"Cercetarea abuzurilor, corupţiei şi pentru petiţii":"Parlament",
"Dezvoltare și strategie economică":"Gazdaság, ipar",
"Transporturi şi energie":"Infrastruktúra, energia, kommunikáció",
"Transporturi şi infrastructură":"Infrastruktúra, energia, kommunikáció",
"Sănătate publică":"Egészésgügy",
"Sănătate şi familie":"Egészésgügy",
"Apărare, ordine publică şi siguranţă naţională":"Állambiztonság",
"Egalitatea de şanse pentru femei şi bărbaţi":"Munka, szociális és családi ügyek",
"Echilibru ecologic şi protecţia mediului":"Közigazgatás, környezetvédelem",
"Industrie şi servicii":"Gazdaság, ipar",
"Mediu şi echilibru ecologic":"Közigazgatás, környezetvédelem",
"Cercetarea abuzurilor, combaterea corupţiei şi petiţii":"Parlament",
"Muncă, sănătate, protecţie socială şi statutul femeii în societate":"Munka, szociális és családi ügyek",
"Administraţie centrală şi locală, amenajarea teritoriului şi urbanism":"Közigazgatás, környezetvédelem",
"Administraţie publică şi amenajarea teritoriului":"Közigazgatás, környezetvédelem",
"Agricultură, silvicultură, industrie alimentară şi servicii pentru agricultură":"Mezőgazdaság, erdők",
"Juridică, de numiri, disciplină, imunităţi şi validări":"Parlament",
"Subcomisia pentru spaţiu":"Közigazgatás, környezetvédelem",
"Cercetarea abuzurilor şi pentru petiţii":"Parlament",
"Muncă, probleme sociale, sănătate":"Munka, szociális és családi ügyek",
"Mediu":"Közigazgatás, környezetvédelem",
"Economică şi pentru problemele de industrie, comerţ, transporturi, telecomunicaţii, servicii":"Infrastruktúra, energia, kommunikáció",
"Constituţionalitate, libertăţi civile şi monitorizare a executării hotărârilor curţii europene a drepturilor omului":"Európa",
"De politică şi pentru drepturile fundamentale ale omului şi cetăţeanului":"Emberi jogok, kisebbségek",
"Românii de pretutindeni":"Külpolitika, diaszpóra",
"Subcomisia pentru monitorizarea executării hotărârilor curţii europene a drepurilor omului":"Emberi jogok, kisebbségek",
"Subcomisia parlamentară pentru romi":"Emberi jogok, kisebbségek",
"Agricultură, industrie alimentară, silvicultură şi protecţia mediului înconjurător":"Mezőgazdaság, erdők",
"Subcomisia pentru protecţia copilului":"Munka, szociális és családi ügyek",
"Subcomisia pentru minoritatea maghiară":"Emberi jogok, kisebbségek",
"Artă, cultură şi mijloace de informare în masă":"Művészet, média",
"Subcomisia pentru demnitate umană":"Emberi jogok, kisebbségek",
"Subcomisia pentru egalitate de tratament şi  nediscriminare":"Emberi jogok, kisebbségek",
"Subcomisia pentru problemele românilor de pretutindeni":"Külpolitika, diaszpóra",
"Subcomisia pe problemele românilor din afara graniţelor":"Külpolitika, diaszpóra",
"Politică financiară, bancară şi bugetară":"Pénzügy",
"Permanentă comună a camerei deputaţilor şi senatului pentru relaţia cu unesco":"Külpolitika, diaszpóra",
"Afaceri europene a parlamentului româniei":"Európa",
"Parlamentară a revoluţionarilor din decembrie 1989":"Állami ügyek",
"Parlamentului româniei pentru integrare europeană":"Európa",
"De redactare a proiectului constituţiei româniei":"Állami ügyek",
"Permanentă a camerei deputaţilor şi senatului privind statutul deputaţilor şi al senatorilor, organizarea şi funcţionarea şedinţelor comune ale camerei deputaţilor şi senatului":"Parlament",
"Comună pentru integrare europeană dintre parlamentul româniei și parlamentul republicii moldova":"Európa",
"Comună permanentă a camerei deputaţilor şi senatului pentru exercitarea controlului parlamentar asupra activităţii sri":"Állambiztonság",
"Apărare şi asigurarea ordinii publice":"Biztonság",
"Parlamentară specială pentru controlul activităţii serviciului de informaţii externe":"Állambiztonság"}

In [1258]:
r2={"Biztonság":"🛃 Biztonság",
"Egészésgügy":"♿️ Egészségügy",
"Emberi jogok, kisebbségek":"🚹 Emberi jogok, kisebbségek",
"Európa":"⏺️ Európa",
"Parlament":"🅿️ Parlament",
"Gazdaság, ipar":"⏫ Gazdaság, ipar",
"Infrastruktúra, energia, kommunikáció":"➿ Infrastruktúra, energia, kommunikáció",
"Közigazgatás, környezetvédelem":"🔄 Közigazgatás, környezetvédelem",
"Külpolitika, diaszpóra":"🌐 Külpolitika, diaszpóra",
"Mezőgazdaság, erdők":"🚰 Mezőgazdaság, erdők",
"Munka, szociális és családi ügyek":"🚻 Munka, szociális és családi ügyek",
"Művészet, média":"🎦 Művészet, média",
"Oktatás, tudomány, sport":"🔠 Oktatás, tudomány, sport",
"Pénzügy":"🔢 Pénzügy",
"Állambiztonság":"🛂 Állambiztonság",
"Állami ügyek":"🔀 Állami ügyek"}

In [1259]:
r3={
'Comisiei pentru tehnologia informaţiei şi comunicaţiilor':"➿ Infrastruktúra, energia, kommunikáció",
 'De validare':"🅿️ Parlament",
 'Subcomisia antidiscriminare':"🚻 Munka, szociális és családi ügyek",
 'Subcomisia pentru egalitatea de şanse pentru copii':"🚻 Munka, szociális és családi ügyek",
 'Subcomisia pentru monitorizarea respectarii drepturilor persoanelor private de libertate':"🚻 Munka, szociális és családi ügyek",
 'Subcomisia pentru oportunităţi egale':"🚻 Munka, szociális és családi ügyek",
 'Subcomisia pentru protecția și promovarea drepturilor persoanelor vârstnice':"🚻 Munka, szociális és családi ügyek",
 'Subcomisia pentru respectarea și apărarea drepturilor și libertăților cetățenilor români aparținând minorității rome':"🚻 Munka, szociális és családi ügyek",
 ' comună a camerei deputaţilor şi senatului pentru controlul bugetului curţii de conturi':'💹 Költségvetés',
 ' comună a camerei deputaţilor şi senatului pentru controlul execuţiei bugetului curţii de conturi pe anul 2000':'💹 Költségvetés',
 ' comună a camerei deputaţilor şi senatului pentru controlul execuţiei bugetului curţii de conturi pe anul 2001 şi 2002':'💹 Költségvetés',
 ' comună a camerei deputaţilor şi senatului pentru elaborarea propunerii legislative de revizuire a constituţiei româniei':'🔀 Állami ügyek',
 ' comună a camerei deputaţilor şi senatului pentru elaborarea propunerilor legislative privind legile electorale':'✅ Választások',
 ' comună a camerei deputaţilor şi senatului pentru elaborarea propunerilor legislative privind legile electorale, propunerilor legislative privind modificarea legii partidelor politice şi a legii privind finanţarea partidelor politice şi a campaniilor electorale.':'✅ Választások',
 ' comună a camerei deputaţilor şi senatului pentru modificarea şi completarea regulamentului şedinţelor comune ale camerei deputaţilor şi senatului':'🅿️ Parlament',
 ' comună a camerei deputaților și senatului pentru avizarea propunerilor legislative depuse și elaborarea unei propuneri legislative privind alegerea camerei deputaților și senatului':'🅿️ Parlament',
 ' comună de anchetă a camerei deputaţilor şi senatului privind cazul «parcul bordei»':'❎ Más',
 ' comună parlamentară de anchetă care să verifice informaţiile furnizate cu privire la interceptarea comunicaţiilor':'🛂 Állambiztonság',
 ' comună specială a camerei deputaţilor şi senatului  pentru controlul execuţiei bugetelor curţii de conturi pe anii 2005, 2006, 2007, 2008 , 2009 şi 2010':'💹 Költségvetés',
 ' comună specială a camerei deputaţilor şi senatului pentru controlul execuţiei bugetului curţii de conturi pe anul 2003':'💹 Költségvetés',
 ' comună specială a camerei deputaţilor şi senatului pentru elaborarea pachetului de legi privind securitatea naţională':'🛂 Állambiztonság',
 ' comună specială a camerei deputaților și senatului pentru examinarea rapoartelor de audit financiar ale curții de conturi și pentru controlul execuției bugetelor anuale ale curții de conturi':'💹 Költségvetés',
 ' comună specială pentru analizarea crizei intervenite în funcţionarea justiţiei':'🔀 Állami ügyek',
 ' de anchetă a camerei deputaţilor pentru analiza situaţiei create la societatea română de televiziune şi societatea română de radiodifuziune prin sistarea de către compania naţională de electricitate - s. a. a alimentării cu energie electrică a unor staţii de emisie':"➿ Infrastruktúra, energia, kommunikáció",
 ' de anchetă a camerei deputaţilor pentru verificarea unor aspecte referitoare la activitatea unor membri din conducerea curţii de conturi':'🔀 Állami ügyek',
 ' de anchetă având drept scop investigarea condiţiilor de legalitate şi de oportunitate privind construirea imobilului «cathedral plaza» în imediata apropiere a catedralei romano-catolice «sfântul iosif» din bucureşti, precum şi a proiectelor de construire şi de sistematizare care afectează zonele istorice din municipiul bucureşti':'❎ Más',
 ' de anchetă parlamentară pentru analiza activităţii ministerului economiei şi comerţului':"⏫ Gazdaság, ipar",
 ' de anchetă pentru investigarea afirmaţiilor cu privire la existenţa unor centre de detenţie ale cia sau a unor zboruri ale avioanelor închiriate de cia pe teritoriul româniei':'🛂 Állambiztonság',
 ' de anchetă pentru verificarea sumelor cheltuite de ministerul turismului pentru acţiuni de promovare a turismului şi a imaginii româniei':"🔄 Közigazgatás, környezetvédelem",
 ' de anchetă privind activitatea sc compania naţională de transporturi aeriene române tarom sa în perioada 2007-2018':"➿ Infrastruktúra, energia, kommunikáció",
 ' de anchetă privind cercetarea condiţiilor în care a fost privatizată societatea comercială balneoclimaterica - s.a. sovata':'❎ Más',
 ' de anchetă privind modul de finanţare a partidelor, formaţiunilor politice şi a candidaţilor la preşedinţia româniei în campaniile electorale din anii 1990, 1992 şi 1996':'🅿️ Parlament',
 ' de anchetă privind modul de reglementare şi supraveghere a pieţei de capital de către  naţională a valorilor mobiliare şi a pieţei monetare de către banca naţională a româniei, pornind de la constatarea stării de încetare de plăţi a fni - sov invest, precum şi pentru verificări la societăţile comerciale cu capital majoritar de stat şi la instituţiile publice implicate în cazul fni - sov invest':"🔢 Pénzügy",
 ' de anchetă privind situaţia economiei forestiere':"🚰 Mezőgazdaság, erdők",
 ' de redactare a proiectului constituţiei româniei':'🔀 Állami ügyek',
 ' de redactare a proiectului de regulament al adunării deputaţilor':'🅿️ Parlament',
 ' de redactare a proiectului de regulament al senatului':'🅿️ Parlament',
 ' elaborarea propunerii legislative privind revizuirea constituţiei':'🔀 Állami ügyek',
 ' elaborarea propunerilor de modificare a regulamentului senatului':'🅿️ Parlament',
 ' parlamentară de anchetă a camerei deputaţilor privind modalitatea de încheiere a unor contracte  de colaborare cu terţe persoane şi a modului de angajare şi efectuarea a cheltuielilor din bani publici în executarea contractelor de colaborare la societatea română de televiziune':"🎦 Művészet, média",
 ' parlamentară de anchetă a camerei deputaţilor şi senatului pentru a clarifica aspectele ce tin de desfiinţarea direcţiei generale de protecţie şi anticorupţie':"🔄 Közigazgatás, környezetvédelem",
 ' parlamentară de anchetă a camerei deputaţilor şi senatului privind activitatea autorităţii naţionale de reglementare în domeniul energiei':"➿ Infrastruktúra, energia, kommunikáció",
 ' parlamentară de anchetă a camerei deputaților și senatului pentru verificarea posibilei implicări a serviciului de protecție și pază în activitatea unor partide politice și în activitatea unor lideri ai acestor partide':'🛂 Állambiztonság',
 ' parlamentară de anchetă instituită în vederea cercetării evenimentelor petrecute în zilele de 13-15 iunie 1990':'🔀 Állami ügyek',
 ' parlamentară de anchetă pentru cercetarea evenimentelor violente desfăşurate în zilele de 23-28 septembrie 1991 în valea jiului, bucureşti şi alte localităţi din ţară':'🔀 Állami ügyek',
 ' parlamentară de anchetă pentru investigarea eventualelor nereguli şi fraude semnalate în spaţiul public cu ocazia derulării procesului electoral la alegerile din 26 mai 2019':'✅ Választások',
 ' parlamentară de anchetă pentru investigarea şi clarificarea modului în care au fost cheltuite sumele din fondul constituit în cotă de 2% din sumele obţinute din privatizări, destinat construcţiei de locuinţe sociale, prevăzut la art.44 alin.(2) din legea nr.10/2001 privind regimul juridic al unor imobile preluate în mod abuziv în perioada 6 martie 1945 - 22 decembrie 1989, republicată':'🔀 Állami ügyek',
 ' parlamentară de anchetă pentru investigări şi clarificări referitoare la activitatea ice dunărea':'❎ Más',
 ' parlamentară de anchetă pentru investigări şi clarificări referitoare la conturile lui nicolae ceauşescu':'🔀 Állami ügyek',
 ' parlamentară de anchetă pentru verificarea legalităţii achiziţiei terenurilor din zona comunei nana, judeţul călăraşi':'❎ Más',
 ' parlamentară de anchetă pentru verificarea modului în care a fost atribuit de către ministerul mediului contractul privind «campania de promovare a programului operaţional sectorial mediu, lot ii - difuzare/publicare» la data de 28 aprilie 2009, prin negociere fără anunţ de participare':'❎ Más',
 ' parlamentară de anchetă pentru verificarea situaţiei societăţii comerciale «nicolina» - s.a. şi a modului în care autoritatea pentru valorificarea activelor statului a gestionat activele acesteia în perioada ianuarie 2005 - decembrie 2008':'❎ Más',
 ' parlamentară de anchetă pentru verificarea sumelor cheltuite de ministerul tineretului şi sportului, sub semnătura doamnei ministru monica iacob-ridzi, pentru organizarea «zilei tineretului»':'🔠 Oktatás, tudomány, sport',
 ' parlamentară de anchetă privind activitatea societăţii române de televiziune':"🎦 Művészet, média",
 ' parlamentară de anchetă privind desfăşurarea procesului de privatizare a societăţilor comerciale de către fondul proprietăţii de stat în anul 1997':'🔀 Állami ügyek',
 ' parlamentară de anchetă privind efectuarea unui control parlamentar asupra activităţii societăţii române de televiziune şi societăţii române de radiodifuziune':"🎦 Művészet, média",
 ' parlamentară de anchetă privind situaţia sistemelor de irigaţii, precum şi a altor sectoare de îmbunătăţiri funciare':"🚰 Mezőgazdaság, erdők",
 ' parlamentară de audiere a persoanelor care de la 22 decembrie 1989 au fost nevoite să-şi părăsească locul de muncă şi domiciliul din judeţele harghita şi covasna':'🔀 Állami ügyek',
 ' parlamentară de audiere a persoanelor de naţionalitate română care de la 22 decembrie 1989 au fost nevoite să-şi părăsească locul de muncă şi domiciliul din judeţele harghita şi covasna':'🔀 Állami ügyek',
 ' parlamentară pentru elaborarea proiectului de hotărâre privind modificarea şi completarea regulamentului şedinţelor comune ale camerei deputaţilor şi senatului':'🅿️ Parlament',
 ' parlamentară specială pentru stabilirea orarului pentru campania electorală şi repartizarea timpilor de antenă':'✅ Választások',
 ' parlamentară specială pentru verificarea îndeplinirii de către ministerul de interne a obligaţiilor legale privind întocmirea listelor electorale permanente şi a cărţilor de alegător, precum şi distribuirea cărţilor de alegător':'✅ Választások',
 ' parlamentară specială referitoare la repartizarea şi monitorizarea timpilor de antenă în vederea campaniei vizând referendumul naţional privind introducerea votului uninominal pentru alegerea membrilor parlamentului româniei':'✅ Választások',
 ' specială a camerei deputaţilor şi senatului pentru atribuirea timpilor de antenă în vederea alegerii membrilor din românia în parlamentul european':'✅ Választások',
 ' specială comună a camerei deputaţilor şi senatului  pentru controlul execuției bugetelor anuale ale curții de conturi':'💹 Költségvetés',
 ' specială comună a camerei deputaţilor şi senatului pentru aderarea româniei la spațiul schengen':"⏺️ Európa",
 ' specială comună a camerei deputaţilor şi senatului pentru celebrarea centenarului marii uniri şi a războiului pentru întregirea neamului':'🔀 Állami ügyek',
 ' specială comună a camerei deputaţilor şi senatului pentru coordonarea activităţilor parlamentare necesare pregătirii preşedinţiei consiliului uniunii europene din primul semestru al anului 2019':"⏺️ Európa",
 ' specială comună a camerei deputaţilor şi senatului pentru elaborarea codului administrativ':'🔀 Állami ügyek',
 ' specială comună a camerei deputaţilor şi senatului pentru eleborarea, modificarea şi completarea propunerilor legislative în materie electorală':'✅ Választások',
 ' specială comună a camerei deputaţilor şi senatului pentru sistematizarea, unificarea şi asigurarea stabilităţii legislative în domeniul justiţiei':'🔀 Állami ügyek',
 ' specială comună a camerei deputaţilor şi senatului privind analizarea şi actualizarea cadrului normativ cu incidenţă în domeniul securităţii naţionale':'🛂 Állambiztonság',
 ' specială comună a camerei deputaților și senatului pentru avizarea proiectului de lege privind unele măsuri aferente exploatării minereurilor auro-argentifere din perimetrul roșia montană și stimularea și facilitarea dezvoltării activităților miniere în românia':"🚰 Mezőgazdaság, erdők",
 ' specială comună pentru dezbaterea în fond, în procedură de urgenţă, a codului penal, a codului de procedură penală, a codului civil şi a codului de procedură civilă':'🔀 Állami ügyek',
 ' specială de anchetă a senatului și camerei deputaților pentru verificarea aspectelor ce țin de organizarea alegerilor din 2009 și de rezultatul scrutinului prezidențial':'✅ Választások',
 ' specială de anchetă a senatului și camerei deputaților privind situația celor două entități energetice, societatea complexul energetic hunedoara și societatea complexul energetic oltenia':"➿ Infrastruktúra, energia, kommunikáció",
 ' specială pentru analiza problemelor economice, sociale şi cele referitoare la condiţiile de viaţă ale minerilor':"⏫ Gazdaság, ipar",
 ' specială pentru avizarea proiectului de lege privind cadastrul general şi publicitatea imobiliară':"🔄 Közigazgatás, környezetvédelem",
 ' specială pentru avizarea proiectului legii privatizării':"🔄 Közigazgatás, környezetvédelem",
 ' specială pentru avizarea propunerii legislative privind minorităţile naţionale şi comunităţile autonome':"🚹 Emberi jogok, kisebbségek",
 ' specială pentru elaborarea proiectului de modificare şi completare a regulamentului senatului':'🅿️ Parlament',
 ' specială pentru elaborarea propunerii legislative privind statutul deputatului şi senatorului':'🅿️ Parlament',
 ' specială pentru elaborarea propunerilor de modificare şi completare a regulamentului camerei deputaţilor':'🅿️ Parlament',
 ' specială pentru elaborarea propunerilor legislative prevăzute la art.79 din legea nr.29/2000 privind sistemul naţional de decoraţii al româniei şi avizarea proiectelor de legi pentru aprobarea ordonanţelor şi ordonanţelor de urgenţă emise de guvern în acest domeniu':'🔀 Állami ügyek',
 ' specială pentru elaborarea unei propuneri legislative cu privire la funcţionarea partidelor politice':'🅿️ Parlament',
 ' specială pentru îmbunătăţirea propunerii legislative privind sistemul de decoraţii al româniei':'🔀 Állami ügyek',
 'comisiei de anchetă având drept scop investigarea condiţiilor de legalitate privind privatizarea societăţii naţionale a petrolului «petrom» - s.a':"➿ Infrastruktúra, energia, kommunikáció",
 'subcomisia de cod civil şi cod de procedură civilă':'🔀 Állami ügyek',
 'subcomisia de cod penal şi cod de procedură penală':'🔀 Állami ügyek',
 ' comună a camerei deputaţilor şi senatului pentru elaborarea propunerii legislative privind alegerea camerei deputaţilor şi a senatului, a preşedintelui româniei, alegerile autorităţilor administraţiei publice locale, finanţarea campaniilor electorale şi alegerea europarlamentarilor':'✅ Választások',
 ' comună de anchetă ca urmare a propunerii de suspendare din funcţie a preşedintelui româniei':'🔀 Állami ügyek',
 ' parlamentară de anchetă privind verificarea unor aspecte referitoare la activitatea preşedintelui curţii de conturi':'🔀 Állami ügyek',
}

In [1289]:
r4={' administraţie publică şi amenajarea teritoriului':'🔄 Közigazgatás, környezetvédelem',
 ' administraţie publică, organizarea teritoriului şi protecţia mediului':'🔄 Közigazgatás, környezetvédelem',
 ' afaceri europene':'⏺️ Európa',
 ' agricultură, silvicultură şi dezvoltare rurală':'🔢 Pénzügy',
 ' buget, finanţe şi bănci':'🔢 Pénzügy',
 ' buget, finanţe, activitate bancară şi piaţă de capital':'🔢 Pénzügy',
 ' cercetarea abuzurilor, combaterea corupţiei şi petiţii':'🔀 Állami ügyek',
 ' cercetarea abuzurilor, corupţiei şi pentru petiţii':'🔀 Állami ügyek',
 ' comună a camerei deputaţilor şi senatului pentru elaborarea propunerii legislative de revizuire a constituţiei românie':'🔀 Állami ügyek',
 ' cultură, arte, mijloace de informare în masă':'🎦 Művészet, média',
 ' drepturile omului, culte şi problemele minorităţilor naţionale':'🚹 Emberi jogok, kisebbségek',
 ' egalitatea de şanse':'🚻 Munka, szociális és családi ügyek',
 ' elaborarea propunerii legislative privind revizuirea constituţie':'🔀 Állami ügyek',
 ' mediu':'🔄 Közigazgatás, környezetvédelem',
 ' muncă şi protecţie socială':'🚻 Munka, szociális és családi ügyek',
 ' parlamentară de anchetă a camerei deputaţilor şi senatului privind activitatea autorităţii naţionale de reglementare în domeniul energie':'➿ Infrastruktúra, energia, kommunikáció',
 ' parlamentară de anchetă pentru verificarea sumelor cheltuite de ministerul tineretului şi sportului, sub semnătura doamnei ministru monica iacob-ridzi, pentru organizarea «zilei tineretului':'💹 Költségvetés',
 ' parlamentară de anchetă privind activitatea societăţii române de televiziun':'🎦 Művészet, média',
 ' parlamentară de audiere a persoanelor de naţionalitate română care de la 22 decembrie 1989 au fost nevoite să-şi părăsească locul de muncă şi domiciliul din judeţele harghita şi covasn':'🔀 Állami ügyek',
 ' parlamentului româniei pentru integrare europeană':'⏺️ Európa',
 ' politică economică, reformă şi privatizare':'🔢 Pénzügy',
 ' politică externă':'🌐 Külpolitika, diaszpóra',
 ' privatizare şi administrarea activelor statului':'💹 Költségvetés',
 ' regulament':'🅿️ Parlament',
 ' specială comună a camerei deputaţilor şi senatului pentru celebrarea centenarului marii uniri şi a războiului pentru întregirea neamulu':'🔀 Állami ügyek',
 ' specială pentru elaborarea propunerilor de modificare şi completare a regulamentului camerei deputaţilo':'🅿️ Parlament',
 ' sănătate şi familie':'♿️ Egészségügy',
 ' învăţământ, ştiinţă, tineret şi sport':'🔠 Oktatás, tudomány, sport',
 'Afaceri europene a parlamentului românie':'🅿️ Parlament',
 'Comună permanentă a camerei deputaţilor şi senatului pentru exercitarea controlului parlamentar asupra activităţii sr':'🛂 Állambiztonság',
 'Constituţionalitate, libertăţi civile şi monitorizare a executării hotărârilor curţii europene a drepturilor omulu':'🚹 Emberi jogok, kisebbségek',
 'Parlamentară a revoluţionarilor din decembrie 198':'🔀 Állami ügyek',
 'Parlamentului româniei pentru integrare european':'⏺️ Európa',
 'Permanentă comună a camerei deputaţilor şi senatului pentru relaţia cu unesc':'UNESCO'}

In [1290]:
def extender(r,n=5):
    p={}
    for i in r:
        for j in range(n):
            p[i+j*' ']=r[i]+j*' '
    return p

In [1291]:
cc={"":"uu",
"/camera_deputatilor/grupuri_prietenie/flags1/africadesud.gif":"za",
"/camera_deputatilor/grupuri_prietenie/flags1/albania.gif":"al",
"/camera_deputatilor/grupuri_prietenie/flags1/algeria.gif":"dz",
"/camera_deputatilor/grupuri_prietenie/flags1/arabiasaudi.gif":"sa",
"/camera_deputatilor/grupuri_prietenie/flags1/argentina.gif":"ar",
"/camera_deputatilor/grupuri_prietenie/flags1/armenia.gif":"am",
"/camera_deputatilor/grupuri_prietenie/flags1/australia.gif":"au",
"/camera_deputatilor/grupuri_prietenie/flags1/austria.gif":"at",
"/camera_deputatilor/grupuri_prietenie/flags1/azerbaidjan.gif":"az",
"/camera_deputatilor/grupuri_prietenie/flags1/bahrein.gif":"bh",
"/camera_deputatilor/grupuri_prietenie/flags1/belarus.gif":"by",
"/camera_deputatilor/grupuri_prietenie/flags1/belgia.gif":"be",
"/camera_deputatilor/grupuri_prietenie/flags1/bolivia.gif":"bo",
"/camera_deputatilor/grupuri_prietenie/flags1/bosnia.gif":"ba",
"/camera_deputatilor/grupuri_prietenie/flags1/brazilia.gif":"br",
"/camera_deputatilor/grupuri_prietenie/flags1/bulgaria.gif":"bg",
"/camera_deputatilor/grupuri_prietenie/flags1/canada.gif":"ca",
"/camera_deputatilor/grupuri_prietenie/flags1/cehia.gif":"cz",
"/camera_deputatilor/grupuri_prietenie/flags1/chile.gif":"cl",
"/camera_deputatilor/grupuri_prietenie/flags1/china.gif":"cn",
"/camera_deputatilor/grupuri_prietenie/flags1/cipru.gif":"cy",
"/camera_deputatilor/grupuri_prietenie/flags1/columbia.gif":"co",
"/camera_deputatilor/grupuri_prietenie/flags1/congo.gif":"cg",
"/camera_deputatilor/grupuri_prietenie/flags1/coreea.gif":"kr",
"/camera_deputatilor/grupuri_prietenie/flags1/costarica.gif":"cr",
"/camera_deputatilor/grupuri_prietenie/flags1/cotedivoir.gif":"ci",
"/camera_deputatilor/grupuri_prietenie/flags1/croatia.gif":"hr",
"/camera_deputatilor/grupuri_prietenie/flags1/cuba.gif":"cu",
"/camera_deputatilor/grupuri_prietenie/flags1/danemarca.gif":"dk",
"/camera_deputatilor/grupuri_prietenie/flags1/ecuador.gif":"ec",
"/camera_deputatilor/grupuri_prietenie/flags1/egipt.gif":"eg",
"/camera_deputatilor/grupuri_prietenie/flags1/elvetia.gif":"ch",
"/camera_deputatilor/grupuri_prietenie/flags1/emirate.png":"ae",
"/camera_deputatilor/grupuri_prietenie/flags1/estonia.gif":"ee",
"/camera_deputatilor/grupuri_prietenie/flags1/filipine.gif":"ph",
"/camera_deputatilor/grupuri_prietenie/flags1/finlanda.gif":"fi",
"/camera_deputatilor/grupuri_prietenie/flags1/franta.gif":"fr",
"/camera_deputatilor/grupuri_prietenie/flags1/georgia.gif":"ge",
"/camera_deputatilor/grupuri_prietenie/flags1/germania.gif":"de",
"/camera_deputatilor/grupuri_prietenie/flags1/grecia.gif":"gr",
"/camera_deputatilor/grupuri_prietenie/flags1/guineea.gif":"gn",
"/camera_deputatilor/grupuri_prietenie/flags1/india.gif":"in",
"/camera_deputatilor/grupuri_prietenie/flags1/indonezia.gif":"id",
"/camera_deputatilor/grupuri_prietenie/flags1/iordania.gif":"jo",
"/camera_deputatilor/grupuri_prietenie/flags1/irak.gif":"iq",
"/camera_deputatilor/grupuri_prietenie/flags1/iran.gif":"ir",
"/camera_deputatilor/grupuri_prietenie/flags1/irlanda.gif":"ie",
"/camera_deputatilor/grupuri_prietenie/flags1/islanda.gif":"is",
"/camera_deputatilor/grupuri_prietenie/flags1/israel.gif":"il",
"/camera_deputatilor/grupuri_prietenie/flags1/italia.gif":"it",
"/camera_deputatilor/grupuri_prietenie/flags1/iugoslavia.gif":"uu",
"/camera_deputatilor/grupuri_prietenie/flags1/japonia.gif":"jp",
"/camera_deputatilor/grupuri_prietenie/flags1/kazahtan.gif":"kz",
"/camera_deputatilor/grupuri_prietenie/flags1/kuwait.gif":"kw",
"/camera_deputatilor/grupuri_prietenie/flags1/letonia.gif":"lv",
"/camera_deputatilor/grupuri_prietenie/flags1/liban.gif":"lb",
"/camera_deputatilor/grupuri_prietenie/flags1/lituania.gif":"lt",
"/camera_deputatilor/grupuri_prietenie/flags1/luxemburg.gif":"lu",
"/camera_deputatilor/grupuri_prietenie/flags1/macedonia.gif":"mk",
"/camera_deputatilor/grupuri_prietenie/flags1/malaezia.gif":"my",
"/camera_deputatilor/grupuri_prietenie/flags1/malta.gif":"mt",
"/camera_deputatilor/grupuri_prietenie/flags1/mareabritanie.gif":"gb",
"/camera_deputatilor/grupuri_prietenie/flags1/maroc.gif":"ma",
"/camera_deputatilor/grupuri_prietenie/flags1/mexic.gif":"mx",
"/camera_deputatilor/grupuri_prietenie/flags1/mongolia.gif":"mn",
"/camera_deputatilor/grupuri_prietenie/flags1/muntenegru.gif":"me",
"/camera_deputatilor/grupuri_prietenie/flags1/norvegia.gif":"no",
"/camera_deputatilor/grupuri_prietenie/flags1/olanda.gif":"nl",
"/camera_deputatilor/grupuri_prietenie/flags1/oman.gif":"om",
"/camera_deputatilor/grupuri_prietenie/flags1/pakistan.gif":"pk",
"/camera_deputatilor/grupuri_prietenie/flags1/panama.gif":"pa",
"/camera_deputatilor/grupuri_prietenie/flags1/peru.gif":"pe",
"/camera_deputatilor/grupuri_prietenie/flags1/polonia.gif":"pl",
"/camera_deputatilor/grupuri_prietenie/flags1/portugalia.gif":"pt",
"/camera_deputatilor/grupuri_prietenie/flags1/qatar.gif":"qa",
"/camera_deputatilor/grupuri_prietenie/flags1/rusia.gif":"ru",
"/camera_deputatilor/grupuri_prietenie/flags1/senegal.gif":"sn",
"/camera_deputatilor/grupuri_prietenie/flags1/singapore.gif":"sg",
"/camera_deputatilor/grupuri_prietenie/flags1/siria.gif":"sy",
"/camera_deputatilor/grupuri_prietenie/flags1/slovacia.gif":"sk",
"/camera_deputatilor/grupuri_prietenie/flags1/slovenia.gif":"si",
"/camera_deputatilor/grupuri_prietenie/flags1/spania.gif":"es",
"/camera_deputatilor/grupuri_prietenie/flags1/srilanka.gif":"lk",
"/camera_deputatilor/grupuri_prietenie/flags1/sudan.gif":"sd",
"/camera_deputatilor/grupuri_prietenie/flags1/suedia.gif":"se",
"/camera_deputatilor/grupuri_prietenie/flags1/thailanda.gif":"th",
"/camera_deputatilor/grupuri_prietenie/flags1/tunisia.gif":"tn",
"/camera_deputatilor/grupuri_prietenie/flags1/turcia.gif":"tr",
"/camera_deputatilor/grupuri_prietenie/flags1/turkmenistan.gif":"tm",
"/camera_deputatilor/grupuri_prietenie/flags1/ucraina.gif":"ua",
"/camera_deputatilor/grupuri_prietenie/flags1/ungaria.gif":"hu",
"/camera_deputatilor/grupuri_prietenie/flags1/urss.gif":"uu",
"/camera_deputatilor/grupuri_prietenie/flags1/usa.png":"us",
"/camera_deputatilor/grupuri_prietenie/flags1/uruguay.gif":"uy",
"/camera_deputatilor/grupuri_prietenie/flags1/venezuela.gif":"ve",
"/camera_deputatilor/grupuri_prietenie/flags1/vietnam.gif":"vn",
"/camera_deputatilor/grupuri_prietenie/flags1/zambia.gif":"zm"}

In [1292]:
cr={'Delegaţia Parlamentului României la Adunarea Parlamentară a Francofoniei':'Frankofónia',
   'Grupul parlamentar de prietenie cu UNESCO':'🇺🇳 UNESCO',
    'Grupul parlamentar de prietenie cu Republica Franceză - Adunarea Naţională':'🇫🇷 Franciaország',
    'Grupul parlamentar de prietenie cu Republica Franceză - Senat':'🇫🇷 Franciaország',
    'Grupul parlamentar de prietenie cu Republica Serbia':'🇷🇸 Szerbia',
    'Delegaţia Camerei Deputaţilor la Adunarea Interparlamentară a Ortodoxiei':'Ortodoxia',
    'Delegaţia Parlamentului României la Adunarea Parlamentară a Consiliului Europei':'Európa Tanács',
    'Delegaţia Parlamentului României la Adunarea Parlamentară a Cooperării Economice a Mării Negre':'Fekete tenger',
    'Delegaţia Parlamentului României la Adunarea Parlamentară a Mediteranei':'Földközi tenger',
    'Delegaţia Parlamentului României la Adunarea Parlamentară a NATO':'NATO',
    'Delegaţia Parlamentului României la Adunarea Parlamentară a OSCE':'OSCE',
    'Delegaţia Parlamentului României la Adunarea Parlamentară a Uniunii pentru Mediterana':'Földközi tenger',
    'Delegaţia Parlamentului României la Adunarea Uniunii Europei Occidentale':'Kelet-Európa',
    'Delegaţia Parlamentului României la Iniţiativa Central-Europeană - Dimensiunea Parlamentară':'Közép-Európa',
    'Delegaţia permanentă a Parlamentului României la Adunarea Parlamentară a Procesului de Cooperare din Europa de Sud-Est':'Délkelet-Európa',
'Grupul mixt de control parlamentar specializat al Europol':'Europol',
   'Comisia Interparlamentară Bucureşti - Chişinău (partea română)':'🇲🇩 Moldova'}

In [1293]:
#!pip install pycountry
import pycountry
import gettext
#!pip install emoji-country-flag
import flag
hun = gettext.translation('iso3166', pycountry.LOCALES_DIR,
                              languages=['hu'])
hun.install()

In [1294]:
def local_country(c):
    if c=='uu': return ''
    z=_(pycountry.countries.get(alpha_2=c.upper()).name)
    #manual overrides
    if z=='Koreai Köztársaság':z='Dél-Korea'
    if z=='Nagy-Britannia (Egyesült Királyság)':z='Egyesült Királyság'
    if z=='Macedón Köztársaság':z='Macedónia'
    if z=='Szíriai Arab Köztársaság':z='Szíria'
    if z=='Venezuelai Bolivári Köztársaság':z='Venezuela'
    if z=='Orosz Föderáció':z='Oroszország'
    g=flag.flagize(':'+c.upper()+':')
    return g+' '+z

In [1295]:
def tolerance_cleaner(ef,dt=30):
    hfs=[]
    df=ef.sort_values('start').groupby(['Típus','Csoportok','start','end']).first()
    df=df.reset_index(level=[2,3], drop=False)
    for p in df.index.get_level_values(0).unique():
        for r in df.loc[p].index.get_level_values(0).unique():
            hf=df.loc[p].loc[[r]].sort_values('start')
            hf['dt']=list((hf[1:]['start']-hf['end'][:-1]).dt.days.values)+[0]
            hf=hf.reset_index(drop=False)
            new_column=[]
            counters={i:0 for i in hf['Csoportok'].unique()}
            for i in hf.index:
                j=hf.loc[i]['Csoportok']
                new_column.append(j+counters[j]*' ')
                if hf.loc[i]['dt']>dt:
                    counters[j]+=1
            hf['Csoportok1']=new_column
            hf['Típus']=p
            hf=hf.drop(['dt'],axis=1)
            hfs.append(hf)
    hfs=pd.concat(hfs)
    hfs=hfs.reset_index(drop=True)
    return(hfs)

In [1296]:
pres_all={'#VP#':'','#PRES#':'','#SECR#':'','#TRES#':'','#SEF#':'','#CHES#':''}

In [1297]:
medals={'#INTER#':'🇺🇳 ','#inter#':'🇺🇳 ','#GRUP#':'🎴 ',
        '#VP#':'🥈','#PRES#':'🥇','#SECR#':'🥉','#TREZ#':'🥉','#PRCV#':'🥉','#SEF#':'🏅','#CHES#':'🏅','#SPEC#':'🚩','#anch#':'🏳️',
        '#vp#':'🥈','#pres#':'🥇','#secr#':'🥉','#trez#':'🥉','#prcv#':'🥉','#sef#':'🏅','#ches#':'🏅','#spec#':'🚩','#anch#':'🏳️',
       }
medals_none={i:'' for i in medals}

In [1298]:
efs=[]
for ni,n in enumerate(nmembers):
    if ni<50:
        if ni%50==0: print(ni/len(nmembers)*100,'%')
        m=nmembers[n]
        data=[]
        since=m['Starts']
        until=m['Ends']
        for p in m['Parties']:
            start=pd.to_datetime(p['start'])
            end=pd.to_datetime(p['end'])    
            d={}
            d['Name']=m['Name']['full']
            party=p['party']
            if '#GRUP#' in party:
                party=group_party_normalizer(party)
            else:
                party=party_normalizer(p['party'])+' '+party_writer(p['party'])+' - '+img['party'][party_writer(p['party'])]['name']
            d['Csoportok']=party
            d['Típus']='Párt'
            d['Image']=img['party'][p['party']]['img']
            d['start']=start
            d['end']=end
            d['duration']=pd.to_timedelta(end-start).days
            data.append(d)
            d=dict(d)
            d['Csoportok']='🇷🇴 '+megyek[p['judet'].capitalize()]
            d['Típus']='Megye'
            data.append(d)
        for p in m['Countries']:
            start=pd.to_datetime(p['start'])
            end=pd.to_datetime(p['end'])    
            d={}
            d['Name']=m['Name']['full']
            d['Csoportok']=p['country']
            d['Típus']='Ország'
            d['Image']=img['state'][replace_all(p['country'],pres_all)]
            d['start']=start
            d['end']=end
            d['duration']=pd.to_timedelta(end-start).days
            data.append(d)
        for p in m['Groups']:
            start=pd.to_datetime(p['start'])
            end=pd.to_datetime(p['end'])    
            d={}
            d['Name']=m['Name']['full']
            d['Csoportok']=p['group'].replace('Comisia pentru','').replace('Comisia','').strip().capitalize()
            d['Típus']='Bizottság'
            d['start']=start
            d['end']=end
            d['duration']=pd.to_timedelta(end-start).days
            data.append(d)

        for pi,p in enumerate(m['Link']):
            start=pd.to_datetime(since[pi])
            end=pd.to_datetime(until[pi])
            d={}
            d['Name']=m['Name']['full']
            d['Típus']='Kamara'
            kamara=m['Camera'][pi]
            pres=''
            if '#' in kamara:
                pres='#'+kamara.split('#')[1]+'#'
                if ('din ') in kamara:
                    b=dict(d)
                    b['Csoportok']=szen[int(p[-1])-1]
                    b['start']=start
                    start=max(start,date_ro(kamara[kamara.find('din ')+4:].strip(),False))
                    b['end']=start
                    b['duration']=pd.to_timedelta(end-start).days
                    data.append(b)
                if ('până în ') in kamara:
                    b=dict(d)
                    b['Csoportok']=szen[int(p[-1])-1]
                    b['end']=end
                    end=min(end,date_ro(kamara[kamara.find('până în ')+8:].strip(),False))
                    b['start']=end
                    b['duration']=pd.to_timedelta(end-start).days
                    data.append(b)
            d['Csoportok']=pres+szen[int(p[-1])-1]
            d['start']=start
            d['end']=end
            d['duration']=pd.to_timedelta(end-start).days
            data.append(d)

        ef=pd.DataFrame(data)
        ef=ef.set_index('Típus').reset_index()
        ef['Simple']=n

        #pres
        csv=ef['Csoportok'].values
        ef['Medals']=[replace_all(i[:i.rfind('#')+1],medals) if '#' in i else '' for i in csv]
        ef['Csoportok']=[replace_all(i,medals_none) for i in csv]

        #committees
        ef=ef.replace(r).replace(r2)

        #countries
        if 'Image' in ef.columns:
            cz={}
            cs=ef[ef['Típus']=='Ország'].groupby('Image').first()['Csoportok']
            for i in sorted(ef[ef['Típus']=='Ország']['Image'].unique()):
                if i in cc:
                    cz[cs.loc[i]]=local_country(cc[i])

            #manual overrides
            cz['Republica Macedonia']='🇲🇰 Macedónia'
            cz['Republica Federală Iugoslavia']='Jugoszlávia'
            cz['fosta Republică Iugoslavă Macedonia']='🇲🇰 Macedónia'
            cz['Grupul parlamentar de prietenie cu fosta Republică Iugoslavă Macedonia']='🇲🇰 Macedónia'
            cz['Republica Franceză - Senat']='🇫🇷 Franciaország'
            cz['Republica Serbia']='🇷🇸 Szerbia'
            cz['Republica Franceză - Adunarea Naţională']='🇫🇷 Franciaország'
            ef=ef.replace(cz).replace(cr)

        #matching
        ef=ef.replace(r3).replace(r4)
        ef['Csoportok9']=ef['Csoportok']
        ef['Csoportok']=ef['Medals']+ef['Csoportok']
        ef['Csoportok']=ef['Csoportok'].replace('','Más').replace('🥈','🥈Más')\
            .replace('🥇','🥇Más').replace('🥉','🥉Más').replace('🏅','🏅Más')

        #unique counting
        new_column=[]
        counters={i:0 for i in ef['Csoportok'].unique()}
        for i in ef['Csoportok']:
            new_column.append(i+counters[i]*' ')
            counters[i]+=1
        ef['Csoportok0']=new_column

        #tolerance
        ef=tolerance_cleaner(ef).reset_index()

        #append
        efs.append(ef)

0.0 %


In [1299]:
efs2=pd.concat(efs)

In [1300]:
efs4=efs2[['start', 'end', 'Name', 'duration',
       'Simple', 'Csoportok','Csoportok0','Csoportok1','Csoportok9', 'Típus','Medals']]

In [1301]:
efs4['Name']=efs4['Name'].str.replace('chestor al Camerei Deputaţilor','')\
    .str.replace('vicepreşedinte al Camerei Deputaţilor','')\
    .str.replace('secretar al Camerei Deputaţilor','')\
    .str.replace('Preşedintele Senatului','')\
    .str.replace('Preşedintele Camerei Deputaţilor','')\
    .str.replace('secretar al Senatului','')\
    .str.replace('chestor al Senatului','')\
    .str.replace('vicepreşedinte al Senatului','')

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  


In [1302]:
sorted([i for i in efs4[((efs4['Típus']=='Párt')&(efs4['Medals']=='🎴 '))]['Csoportok9'].unique()])

['⚪️ FSN',
 '✳️ PNTCD',
 '🌷 RMDSZ',
 '🌹 PSD',
 '👤 Independent',
 '👤 Minorități',
 '📐 PAC',
 '📐 PNL',
 '🔱 PRM',
 '🔶 PD',
 '🔶 PDL',
 '🕊️ ALDE',
 '🕊️ PC',
 '🕊️ PUNR',
 '\U0001f9d1 PRO Europa']

In [1304]:
sorted([i for i in efs4[(efs4['Típus']=='Bizottság')]['Csoportok9'].unique()])

[' agricultură, silvicultură, industrie alimentară şi servicii specifice',
 ' apărare, ordine publică şi siguranţă naţională',
 ' comună a camerei deputaţilor şi senatului pentru controlul bugetului curţii de contur',
 ' comună a camerei deputaţilor şi senatului pentru elaborarea propunerilor legislative privind legile electoral',
 ' comună a camerei deputaţilor şi senatului pentru modificarea şi completarea regulamentului şedinţelor comune ale camerei deputaţilor şi senatulu',
 ' comună de anchetă a camerei deputaţilor şi senatului privind cazul «parcul bordei',
 ' comună permanentă a camerei deputaţilor şi senatului pentru exercitarea controlului parlamentar asupra activităţii sri',
 ' comună specială a camerei deputaţilor şi senatului pentru controlul execuţiei bugetului curţii de conturi pe anul 200',
 ' comună specială a camerei deputaţilor şi senatului pentru elaborarea pachetului de legi privind securitatea naţional',
 ' de anchetă parlamentară pentru analiza activităţii ministe

In [1306]:
efs4

start        end                 Name  duration  \
0  2016-12-21 2019-07-01  Tamara-Dorina CIOFU       922   
1  2012-12-20 2016-12-21  Tamara-Dorina CIOFU      1462   
2  2012-12-20 2016-12-21  Tamara-Dorina CIOFU      1462   
3  2012-12-20 2016-12-21  Tamara-Dorina CIOFU      1462   
4  2019-03-01 2019-07-01  Tamara-Dorina CIOFU       122   
5  2012-12-20 2013-03-01  Tamara-Dorina CIOFU        71   
6  2012-12-20 2016-12-21  Tamara-Dorina CIOFU      1462   
7  2016-12-21 2019-07-01  Tamara-Dorina CIOFU       922   
8  2013-03-01 2016-12-21  Tamara-Dorina CIOFU      1391   
9  2016-12-21 2019-03-01  Tamara-Dorina CIOFU       800   
10 2012-12-20 2016-12-21  Tamara-Dorina CIOFU      1462   
11 2016-12-21 2019-07-01  Tamara-Dorina CIOFU       922   
12 2012-12-20 2016-12-21  Tamara-Dorina CIOFU      1462   
13 2016-12-21 2019-07-01  Tamara-Dorina CIOFU       922   
14 2016-12-21 2019-07-01  Tamara-Dorina CIOFU       922   
15 2012-12-20 2016-12-21  Tamara-Dorina CIOFU      1462   
16 2012-12-20 2016-12-21  Tamara-Dorina CIOFU      1462   
17 2012-12-20 2016-12-21  Tamara-Dorina CIOFU      1462   
18 2016-12-21 2019-07-01  Tamara-Dorina CIOFU       922   
19 2016-12-21 2019-07-01  Tamara-Dorina CIOFU       922   
20 2012-12-20 2016-12-21  Tamara-Dorina CIOFU      1462   
21 2016-12-21 2019-07-01  Tamara-Dorina CIOFU       922   
22 2012-12-20 2016-12-21  Tamara-Dorina CIOFU      1462   
23 2016-12-21 2019-07-01  Tamara-Dorina CIOFU       922   
0  1990-06-18 1992-10-16    Gheorghe MUNTEANU       851   
1  1990-06-18 1992-10-16    Gheorghe MUNTEANU       851   
2  1990-06-18 1992-10-16    Gheorghe MUNTEANU       851   
3  1990-06-18 1992-10-16    Gheorghe MUNTEANU       851   
4  1990-06-18 1992-10-16    Gheorghe MUNTEANU       851   
5  1990-06-18 1992-10-16    Gheorghe MUNTEANU       851   
..        ...        ...                  ...       ...   
8  2012-07-01 2012-12-20           Mihai NIŢĂ       172   
9  2012-12-20 2016-12-21           Mihai NIŢĂ      1462   
10 2016-12-21 2019-07-01           Mihai NIŢĂ       922   
11 2008-12-19 2012-12-20           Mihai NIŢĂ      1462   
12 2016-12-21 2019-07-01           Mihai NIŢĂ       922   
13 2016-12-21 2019-07-01           Mihai NIŢĂ       922   
14 2012-12-20 2016-12-21           Mihai NIŢĂ      1462   
15 2008-12-19 2012-12-20           Mihai NIŢĂ      1462   
16 2012-12-20 2016-12-21           Mihai NIŢĂ      1462   
17 2016-12-21 2019-07-01           Mihai NIŢĂ       922   
18 2008-12-19 2012-12-20           Mihai NIŢĂ      1462   
19 2008-12-19 2012-12-20           Mihai NIŢĂ      1462   
20 2012-12-20 2016-12-21           Mihai NIŢĂ      1462   
21 2012-07-01 2012-12-20           Mihai NIŢĂ       172   
22 2008-12-19 2012-07-01           Mihai NIŢĂ      1290   
23 2016-12-21 2019-07-01           Mihai NIŢĂ       922   
24 2012-12-20 2016-12-21           Mihai NIŢĂ      1462   
25 2008-12-19 2012-07-01           Mihai NIŢĂ      1290   
26 2016-12-21 2019-07-01           Mihai NIŢĂ       922   
27 2012-07-01 2012-12-20           Mihai NIŢĂ       172   
28 2012-12-20 2016-12-21           Mihai NIŢĂ      1462   
0  2012-12-20 2013-05-01        George BECALI       132   
1  2012-12-20 2013-05-20        George BECALI       151   
2  2012-12-20 2013-02-01        George BECALI        43   
3  2012-12-20 2013-05-20        George BECALI       151   
4  2013-02-01 2013-05-20        George BECALI       108   
5  2012-12-20 2013-05-01        George BECALI       132   
6  2012-12-20 2013-05-20        George BECALI       151   
7  2013-02-01 2013-05-20        George BECALI       108   
8  2012-12-20 2013-02-01        George BECALI        43   

                              Simple  \
0   Ciofu Tamara-Dorina | 1957-12-30   
1   Ciofu Tamara-Dorina | 1957-12-30   
2   Ciofu Tamara-Dorina | 1957-12-30   
3   Ciofu Tamara-Dorina | 1957-12-30   
4   Ciofu Tamara-Dorina | 1957-12-30   
5   Ciofu Tamara-Dorina | 1957-12-30   
6   Ciofu Tamara-Dorina | 1957-12-30   
7   Ciofu Tamara-Dorina | 195

In [1305]:
efs4[efs4['Simple']=='Popescu-Tariceanu Calin Constantin Anton | 1952-01-14']

Empty DataFrame
Columns: [start, end, Name, duration, Simple, Csoportok, Csoportok0, Csoportok1, Csoportok9, Típus, Medals]
Index: []

In [410]:
j=efs4.reset_index().drop('index',axis=1).T.astype(str).to_dict()
open('ignore/member_timelines.json','w').write(json.dumps(list(j.values())))

19784035

In [411]:
len(efs4['Simple'].unique())

2818

In [412]:
import zipfile

with zipfile.ZipFile("json/member_timelines.zip", "w", compression=zipfile.ZIP_DEFLATED) as zf:
    zf.write("ignore/member_timelines.json","member_timelines.json")

In [413]:
members={}
simple={}
simple2={}
for i in efs4[['Name','Simple']].T.iteritems():
    if i[1][0] not in simple: simple[i[1][0]]=i[1][1]
    if i[1][1] not in simple2: simple2[i[1][1]]=i[1][0]
members['s']=simple
members['s2']=simple2

In [414]:
members['megye']=efs4[efs4['Típus']=='Megye'].sort_values(by='start')[['Simple','Csoportok']].set_index('Csoportok')\
    .drop_duplicates(keep='last').reset_index().set_index('Simple')['Csoportok'].to_dict()

In [415]:
members['part']=efs4[efs4['Típus']=='Párt'].sort_values(by='start')[['Simple','Csoportok']].set_index('Csoportok')\
    .drop_duplicates(keep='last').reset_index().set_index('Simple')['Csoportok'].to_dict()

In [416]:
members['deaths']=deaths

Vega direct plot

In [417]:
m='Popescu-Tariceanu Calin Constantin Anton | 1952-01-14'
ef=efs4[efs4['Simple']==m]
viz=alt.Chart(ef,
          title=m
         ).mark_bar().encode(
    x=alt.X('start:T',title=''),
    x2='end:T',
    y=alt.Y('Csoportok:N',title='',
            sort=alt.EncodingSortField(field="order", op="mean", order='descending')),
    color=alt.Color('Típus:N',
        sort=alt.EncodingSortField(field="order", op="mean", order='descending'))
)
# viz.save('json/viz.json')
viz.interactive()

<VegaLite 3 object>

If you see this message, it means the renderer has not been properly enabled
for the frontend that you are using. For more information, see
https://altair-viz.github.io/user_guide/troubleshooting.html


Member images

In [418]:
photos={name:nmembers[name]['Photo'][np.array([p[-10:-6] for p in nmembers[name]['Link']]).argmax()] for name in nmembers}

Download photos if you need to..

In [1221]:
import urllib.request

In [ ]:
#downloader - run once only
for p in photos:
    urllib.request.urlretrieve(photos[p], "photos3/"+p.replace('|','+')+'.jpg')

In [ ]:
from PIL import Image
#!pip install python-resize-image
from resizeimage import resizeimage

In [ ]:
err=[]
for p in photos:
    try:
        img = Image.open('photos3/'+p.replace('|','+')+'.jpg', 'r')
        img = resizeimage.resize_cover(img, [123,150])
        img.save('photos4/'+p.replace('|','+')+'.jpg', img.format)
    except:
        print(p)
        err.append(p)

In [ ]:
#run this then iterate cell above until no errors
for p in err:
    urllib.request.urlretrieve(photos[p], "photos3/"+p.replace('|','+')+'.jpg')

In [ ]:
for p in err:
    try:
        img = Image.open('photos3/'+p.replace('|','+')+'.jpg', 'r')
        img = resizeimage.resize_cover(img, [123,150])
        img.save('photos4/'+p.replace('|','+')+'.jpg', img.format)
    except:
        img = Image.open('photos3/'+p.replace('|','+')+'.jpg', 'r')
        img.save('photos4/'+p.replace('|','+')+'.jpg', img.format)

Otherwise continue here:

In [419]:
members['photo']={p:'photos4/'+p.replace('|','+')+'.jpg' for p in photos}

In [420]:
open('ignore/member_simple.json','w').write(json.dumps(members))

958702

In [421]:
import zipfile

with zipfile.ZipFile("json/member_simple.zip", "w", compression=zipfile.ZIP_DEFLATED) as zf:
    zf.write("ignore/member_simple.json","member_simple.json")

In [422]:
pretty={'- din care declaraţii politice':'🧾 Nyilatkozatok',
        'Declaraţii politice depuse în scris':'🧾 Nyilatkozatok',
       'Luari de cuvânt':'🎙️ Felszólalások', 
        'Luari de cuvânt în BP':'🎙️ Felszólalások', 
        'Motiuni':'📚 Javaslatok', 
        'Proiecte de hotarâre initiate':'📚 Javaslatok', 
        'Propuneri legislative initiate':'📚 Javaslatok',
        'Sedințe':'💺 Ülések', 
        'Întrebari si interpelari':'🎙️ Felszólalások'}

In [423]:
efx=[]
for n in nmembers:
    m=nmembers[n]
    data=[]
    since=m['Starts']
    until=m['Ends']
    for pi in range(len(m['Link'])):
        p=m['Link'][pi]
        d={}
        d['Simple']=n
        d['Link']=p
        d['Session']=p[-10:-6]
        for a in m['Activity']:
            if type(m['Activity'][a])==list:
                g=m['Activity'][a]
            else:
                g=[m['Activity'][a]]
            for h in g:
                if h['start']==since[pi]: 
                    if pretty[a] not in d:d[pretty[a]]=0
                    d[pretty[a]]+=h['value']
        data.append(d)
    ef=pd.DataFrame(data)

    #append
    efx.append(ef)

In [424]:
efx2=pd.concat(efx).fillna(0).reset_index().drop('index',axis=1)

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:1: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  """Entry point for launching an IPython kernel.


In [425]:
j=efx2.T.astype(str).to_dict()
j2=list(j.values())

In [426]:
j3={}
for i in j2:
    if i['Simple'] not in j3:j3[i['Simple']]=[]
    j3[i['Simple']].append(i)

In [427]:
open('ignore/member_activity.json','w').write(json.dumps(j3))

1433467

In [428]:
import zipfile

with zipfile.ZipFile("json/member_activity.zip", "w", compression=zipfile.ZIP_DEFLATED) as zf:
    zf.write("ignore/member_activity.json","member_activity.json")